# Exploratory analysis of LBMP data
This notebook includes a handfull of figures looking at basic characteristics and trends of the NYC LBMP data in 2017. It is not intended to be a complete analysis, just a quick overview to better understand the price data.

In [46]:
import pandas as pd
import altair as alt
import pytz
from pathlib import Path
from src.read_data import read_all_nyc
from src.read_all_NL import read_all_NL


# Select your appropriate notebook type for rendering Altair figures
alt.renderers.enable('jupyterlab')
# alt.renderers.enable('notebook')
alt.data_transformers.enable('default', max_rows=None)

DataTransformerRegistry.enable('default')

## Import data and add temporal columns

In [47]:
#data_path = Path.cwd() / '2017_NYISO_LBMPs'
#df = read_all_nyc(data_path)

df = read_all_NL()

In [48]:
# Drop the first hour, which is part of 2016 week 52
#df = df.loc[df.time_stamp >= '2023-01-01', :]

# Ensure 'time_stamp' is in datetime format, and if it's timezone-aware, convert it to UTC first
df['time_stamp'] = pd.to_datetime(df['time_stamp'], utc=True)

# Convert to Amsterdam timezone
amsterdam_tz = pytz.timezone('Europe/Amsterdam')
df['time_stamp'] = df['time_stamp'].dt.tz_convert(amsterdam_tz)

In [49]:
df['week'] = df.time_stamp.dt.isocalendar().week
df['month'] = df.time_stamp.dt.month
df['quarter'] = df.time_stamp.dt.quarter
df['hour_of_day'] = df.time_stamp.dt.hour
df['day_of_week'] = df.time_stamp.dt.dayofweek

In [50]:
df.head()

time_stamp  lbmp  hour  week  month  quarter  hour_of_day  \
0 2023-01-01 00:00:00+01:00 -3.61     0    52      1        1            0   
1 2023-01-01 01:00:00+01:00 -1.46     1    52      1        1            1   
2 2023-01-01 02:00:00+01:00 -1.52     2    52      1        1            2   
3 2023-01-01 03:00:00+01:00 -5.00     3    52      1        1            3   
4 2023-01-01 04:00:00+01:00 -4.60     4    52      1        1            4   

   day_of_week  
0            6  
1            6  
2            6  
3            6  
4            6

## Data exploration

Lets start by looking at the distribution of NYC LBMP values in 2017. From the figure below it appears that most values are between \\$20 and \\$40 dollars, very few values are below \\$10, and prices occasionally go above \\$100.

In [51]:
alt.Chart(df).mark_bar().encode(
    alt.X('lbmp:Q', bin=alt.Bin(step=25)),
    y='count()'
)

<VegaLite 5 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/display_frontends.html#troubleshooting


Since hourly prices are skewed and have a long(ish) tail, lets use a heatmap to look at the median hourly LBMP for every week of the year. This will help determine if high prices tend to show up during certain times of the day or year.

There may be some within-day trends, but they don't seem to hold for the all weeks of the year. Median prices are often lowest in early morning hours. Some periods of the year see an early afternoon dip in prices, but afternoon hours have the highest prices in other weeks. Futher investigation would be needed to identify potential causal factors.

Week 11 has higher than normal prices, but week 52 is the real outlier. Median prices in that week are always above \\$85.

In [52]:
alt.Chart(df).mark_rect().encode(
    x='week:O',
    y='hour_of_day:O',
    color=alt.Color('median(lbmp):Q', sort='descending'),
    tooltip='median(lbmp):Q'
)

<VegaLite 5 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/display_frontends.html#troubleshooting


Grouping the same data by quarter and day of week rather than week of year helps to show some basic differences across the year and on weekdays vs weekends.

In [57]:
alt.Chart(df).mark_rect().encode(
    x='day_of_week:O',
    y='hour_of_day:O',
    column='month:O',
    color=alt.Color('median(lbmp):Q', sort='descending')
)

<VegaLite 5 object>

If you see this message, it means the renderer has not been properly enabled
for the frontend that you are using. For more information, see
https://altair-viz.github.io/user_guide/display_frontends.html#troubleshooting
